# Brownian Motion Example
Demonstration of how to use trkpy to extract particle trajectories.

Information mostly from here:
http://soft-matter.github.io/trackpy/v0.4.2/tutorial/walkthrough.html

Depending on where you are running this, you may need to add trkpy and pims to your python modules.

Note: this notebook will *not* give you good results as-is.  You need to tune the particle ID parameters to give good results on your particular video!

Updated 10/1/19 to work with pims v0.4

Updated 10/27/20 to include check on sub-pixel accuracy


In [ ]:
# Import the packages we need
import math
import pims
import trackpy as tp
import numpy as np
import pandas as pd
from pandas import DataFrame, Series  # for convenience
import matplotlib.pyplot as plt

# Don't know if this is necessary
%matplotlib inline
plt.rcParams['image.cmap'] = 'gray'  # Set grayscale images as default.

Read in a movie using the pims package.  Videos are split into single frames.  Adjust the file path to match the location of your movie files.

In [ ]:
frames = pims.PyAVReaderIndexed('data/bm_x100_1_02_um_d_1s_v3.mov')

An alternative approach is to first split the movie into jpeg files using a command-line tool ffmpeg:

`mkdir frames`

`ffmpeg -i "filename.mov" -f image2 "frames/video-frame%05d.png"`

Then, instead of `PyAVReader` you can use:

`frames = pims.ImageSequence('frames/*.png')`

### Greyscale
Movies are color by default, use this code to convert to greyscale.  This improves the contrast in each image.

In [ ]:
from pims import pipeline

@pipeline
def as_grey(frame):
    red = frame[:, :, 0]
    green = frame[:, :, 1]
    blue = frame[:, :, 2]
    return 0.2125 * red + 0.7154 * green + 0.0721 * blue


Can look at a single frame to make sure this worked.

In [ ]:
as_grey(frames[10])

Convert the entire video into greyscale, then each frame can be accessed just like any other array.  

This command doesn't actually do any processing, the processing will happen 'on the fly' as each frame is needed.  This is what the 'pipeline' directive in the code above is used for.

In [ ]:
processed_video = as_grey(frames)

In [ ]:
processed_video[0]

## Particle Identification
trkpy.locate will find 'features' for us.  We need to tune the parameters a bit to get something reasonable.  The diameter (which must be an odd number) should match the size of the feature you want to find in pixels, minmass sets a lower limit on the brightness, an invert=True can be used to find dark features rather than light features.  You may not need invert depending on the lighting in your video.

Play around with these parameters until you are able to find a reasonable number of beads in each frame.  Each bead will be drawn with a red circle around it.  If you get lots of red, try increasing the minmass parameter.

Finding less particles is better than more, as we would like to avoid too many out-of-focus particles.

In [ ]:
iframe=10

# Vary these parameters to find the particles
diam = 7
mass = 20
df = tp.locate(processed_video[iframe], diameter=diam, minmass=mass, invert=True)

plt.figure()
tp.annotate(df, processed_video[iframe]);

The df object is a pandas dataframe.  We can plot the attributes, particularly the mass, to find a good lower limit on this value.  Adjust the value of minmass above until you have removed any low-mass noise or badly imaged beads.  

In [ ]:
plt.hist(df['mass'], bins=20)
plt.xlabel('Particle Mass')
plt.show()

You can also just print out the extracted dataframe to see what other information you have available.

In [ ]:
df.head()

Once you have a reasonable set of parameters for trkpy.locate, apply that to all of the frames in the video with trkpy.batch.  Make sure you use the same parameters as above.  The 'features' found per frame should be fairly constant.  If there are frames with no features, or lots of features, check those frames individually.  Changing lighting conditions can really screw this up.  If only a range of your video is OK, use array indexing on processed_video to just use a subset of the frames.

In [ ]:
df = tp.batch(processed_video, diameter=diam, minmass=mass, invert=True);

### Sub-pixel accuracy

Check for sub-pixel accuracy.  This plots the 10ths value of each particle position.  It should be random.  If there is a dip in these distributions, our diameter used above is too small, and the extracted positions are lining up on the pixel centers.  A slight dip is OK, but it shouldn't be overly apparent.  Go back and change your diameter and mass settings until these distributions come out mostly flat.

In [ ]:
tp.subpx_bias(df)

## Finding Trajectories
Now we want to combine features in different frames into particle trajectories.
Search_range specifies how far the particle can move between frames and still be considered the same particle.  If this is too small you will underestimate your diffusion.  If this is too large, your code will take forever to run...  Memory specifies how many frames can be skipped (where the particle isn't found).  Use memory=0 or you will have problems below.

In [ ]:
rawt = tp.link_df(df, search_range=10, memory=0)

You may have a large number of short stubs in your raw trajectories.  Filter these by requiring at least 10 consecutive frames.  This should reduce the total trajectories to a more reasonable number.

In [ ]:
# Require a feature in at least 10 consecutive frames
traj = tp.filter_stubs(rawt, 10)
# Compare the number of particles in the unfiltered and filtered data.
print('Before:', rawt['particle'].nunique())
print('After:', traj['particle'].nunique())

We can now make a pretty plot of our trajectories. If you don't get nice long trajectories, your search range might be too small, or your video just doesn't have very good contrast.

In [ ]:
plt.figure()
tp.plot_traj(traj);

### Drifts
If your plot above shows evidence of a collective drift, you can remove it using this function.  This may cause more problems than it fixes, however, so you may want to avoid it.  This computes the average motion between frames, that can then be subtracted from your trajectories.

In [ ]:
d = tp.compute_drift(traj)
d.plot()
plt.show()

Now we can subtract the average overall drift.  I would only do this if you have significant drift of more than half a pixel per frame.

In [ ]:
# Subtract the drift
# tm = tp.subtract_drift(traj.copy(), d)

# ... or not
tm = traj

Lets look at the results here again

In [ ]:
plt.figure()
tp.plot_traj(tm);

Again, this is just a dataframe, so we can print what we have.  Note the particle entry, which identifies each individual trajectory.

In [ ]:
tm.head()

The particle numbering doesn't necessarily follow any logic.  We can see the unique set of particle numbers as follows.

In [ ]:
print(set(tm['particle']))

Try to find a single trajectory that has a lot of data and isn't stuck in one position.  You can either do this by going through the particle numbers (shown first) or by selecting out a trajectory using positions.  Some combination of both works also.

Here I am printing the length of each trajectory, which can help to find a good one.  I am also saving all the found trajectories into one sorted list for processing later.

In [ ]:
trajectory_list = []

# Loop over the unique particle numbers
for tnum in set(tm['particle']):
    the_trajectory = tm[(tm['particle']==tnum)]
    trajectory_list.append(the_trajectory)
    
# Sort by trajectory length and print the first five
trajectory_list.sort(key=len, reverse=True)
for t in trajectory_list[0:10]:
    print("Trajectory",t['particle'].values[0],"has length",len(t))

Now you can pick out a few by particle number and see how they look

In [ ]:
t1 = tm[(tm['particle']==1733)]
plt.figure()
tp.plot_traj(t1);

You can also try to select trajectories by location in the frame, but if you have a lot of overlapping trajectories, this won't work very well.

In [ ]:
t2 = tm[((tm['x']>150) & (tm['x']<250) & (tm['y']>400))]
plt.figure()
tp.plot_traj(t2);

You can also check where your selected particle is in any given frame as follows.  This only works if you did not subtract off any drift.

In [ ]:
iframe=250
plt.figure()
tp.annotate(t1[t1['frame'] == iframe], frames[iframe]);

## Extracting position information
Again, we really just have a data frame now selected for one specific particle.  We want to extract the x and y positions from this (and really the difference in x and y positions between frames).

In [ ]:
t1.head()

It is probably easiest to write the x and y positions of your bead to a CSV file which you can then analyze later.  The following command will do that for you.  This can then be read back easily using pandas.  You can also save the entire dataframe if you wish (not just the x and y coordinates).

In [ ]:
t1[['x','y']].to_csv('filename.csv')

This code will extract the five longest trajectories and write them to their own files.

In [ ]:
for t in trajectory_list[0:10]:
    tnum = t['particle'].values[0]
    filename = f"trajectory_{tnum}.csv"
    t[['x','y']].to_csv(filename)
    print(f"Wrote file {filename}")

We can also write the entire trajectory dataframe in case you want to analyze all of the trajectories (this isn't necessary).  You can read this back in using the from_csv() function as we saw in Lab 1.

In [ ]:
tm.to_csv('trajectory_frame.csv')

## Data Analysis

You should start your analysis in a different notebook, but to help you get started, I will show you how to extract arrays from the dataframe and make a simple histogram of the position differences between video frames.  

There are probably more 'pandas-like' ways to do this, but a simple trick to find the difference between successive elements in a vector is to take the difference between a subset of the vectors with different offsets.  This method insures that the two vectors used in making the diff are the same length.

In [ ]:
# Turn the dataframe into a simple vector using values
xvec = t1['x'].values
# Find the difference in xvec by some number of frames in the video 
offset = 1
xdiff = xvec[offset:]-xvec[:-offset]

Now we have an array of $\Delta x$ differences (separated by $\Delta t$ determined by the offset parameter and the frame rate of the video) which we can use to make a histogram and find the standard deviation.  Note that distance is still measured in pixels.  You will need to calibrate this to get a physically meaningful diffusion.

In [ ]:
plt.hist(xdiff, 20)
plt.xlabel('Delta x (pixels)')
plt.show()
sdx = np.std(xdiff)
print (f"SD x: {sdx:.3} pixels")

The next steps are up to you.  You will need to do something similar to get the $\Delta y$ distribution, then decide how to combine these to find the diffusion coefficient.  You could also add more data by looking at other beads.  Adjusting the offset will allow you to extract data to demonstrate the linear growth in diffusion with time.